# Homework 6
- Xander Smeets (1325523, x.l.j.a.smeets@student.tue.nl)
- Ruben Biskupec (1878638, r.biskupec@student.tue.nl)
- Tom Lin (1909150, t.lin@student.tue.nl)

## Exercise 1
Exercise 1 is handed in as a separate PDF file with this assignment.

## Exercise 2

### Exercise 2a

In [1]:
# The following values are given in the exercise.
p = 541
q = 733
(n, e) = 396553, 17

In [2]:
phi_n = (p-1)*(q-1)

In [3]:
def mod_inv(a, b):
    return Mod(xgcd(a,b)[1], b)

In [4]:
d = Mod(1/e, phi_n)
assert mod_inv(e, phi_n) == d

In [5]:
dp = Mod(d, p-1)
dq = Mod(d, q-1)
assert mod_inv(e, p-1) == dp
assert mod_inv(e, q-1) == dq

# See the note at the bottom of this exercise to see why we are casting results back to integers.
dp = int(dp)
dq = int(dq)

In [6]:
# Note that we need for this that p < q. Otherwise, we would probably need to swap p and q first.
u = Mod(1/p, q)
assert mod_inv(p, q) == u

# Once again, we cast the result to an integer.
u = int(u)

In [7]:
(n, p, q, dp, dq, u)

(396553, 541, 733, 413, 689, 691)

### Exercise 2b

Note that decrypting is the same as signing in RSA. Hence, we can simply compute the 'signature' of the ciphertext to retrieve the message. Similarly, to compute the re-encryption, we can apply the verification techniques once again.

In [8]:
# The ciphertext given in the exercise is
c = 234040

What follows has been based on [the final slide for RSA-II](https://hyperelliptic.org/tanja/teaching/crypto21/rsa-2.pdf#page=12).

In [9]:
cp = int(Mod(c, p))
cq = int(Mod(c, q))

In [10]:
# Note: in Python, ** is the symbol for exponentiation (i.e. raising to a power)
# However, SageMath seems to accept ^ as well, see e.g. https://doc.sagemath.org/html/en/prep/Quickstarts/Number-Theory.html#modular-arithmetic
mp = int(Mod(cp ^ dp, p))
mq = int(Mod(cq ^ dq, q))

<div class="alert alert-info">
    Note that, in the cell above, we need to explicitly cast these as integers; otherwise, SageMath will complain due to the integers not being taken in the same ring in the next cell.
</div>

In [11]:
m = int(Mod(mp + p*u*(mq-mp), n))
m

332211

Next, we need to verify our result by re-encrypting it. For this, we use the 'usual' (i.e. non-CRT-enhanced) method of encryption to obtain the following

In [12]:
m_reencrypted = int(Mod(m ^ e, n))
m_reencrypted

234040

In [13]:
if (int(c) == int(m_reencrypted)):
    print("The result seems to be in order.")
else:
    print("Something has gone wrong...")

The result seems to be in order.


<div class="alert alert-danger">
    It seems that casting all intermediate results back to integers is <strong>essential</strong> when working in SageMath; otherwise, variables seem to be interpreted as integers on the ring of integers modulo 'some value', which seems to give different results.
</div>

## Exercise 3

### Exercise 3a

In [14]:
n = 396553
a = 8
s = lcm([1,2,3,4,5,6,7,8,9,10,11,12])

# We need to state the value for s
s

27720

In [15]:
b = Mod(a ^ s, n)
b

192056

In [16]:
p = int(gcd(b-1, n))
p

541

<div class="alert alert-success">
    Since this output value is not $1$ or $n$, we can output this output value; it is one of the factors of $n$.
</div>
To compute the second factor, we simply divide $n$ by the first factor.

In [17]:
q = int(int(n) / p)
q

733

To check our result, we compute $p\cdot q$ and check whether it is equal to $n$.

In [18]:
if (p * q == n):
    print("p*q = " + str(p*q) + " = n")
else:
    print(str(p*q) + " = p*q ≠ n = " + str(n))

p*q = 396553 = n


<div class="alert alert-info">
    Thus, we have that the factors of $n=396553$ are given by $p=541$ and $q=733$.
    <br><br>
    The intermediate results are given by $s=27720$ and $b=192056$.
</div>

### Exercise 3b

#### Part 1

<div class="">
    Note: for this exercise, we are not entirely sure on how to incorporate our knowledge of the factors of $p-1$ and $q-1$ into the exercise. Therefore, we explain the results. in two different ways:
    <ol>
        <li>In this first part, we will simply look at the order of $a$ in the multiplicative groups of integers $\mod p$ and $\mod q$, $\mathbb{F}_p^*$ and $\mathbb{F}_q^*$.</li>
        <li>In the second part, we investigate a different reasoning which does consider the factors of $p-1$ in particular.</li>
    </ol>
</div>

For the first part, let's start by seeing whether taking $a=2$ would have worked, as suggested in the hint.

In [19]:
a = 2
b = Mod(a ^ s, n)
p_2 = int(gcd(b-1, n))
p_2

1

<div class="alert alert-warning">
    This gives us the value $1$, for which we know that it is not a (non-trivial) factor of $n$. Hence, the $p-1$ method would indeed not have worked with $a=2$.
</div>

We know that the $p-1$ method works only when the following two conditions are met:
<ol>
    <li>$p$ divides $a^s-1$, which holds if and only if the order of $a$ in $\mathbb{F}_p^*$ divides $s$.</li>
    <li>$q$ does <strong>not</strong> divide $a^s-1$. Thus, we must have that the order of $a$ in $\mathbb{F}_q^*$ does not divide $s$.</li>
</ol>

Furthermore, we must not have that the order of $a$ in $\mathbb{F}_p^*$ is equal to $1$; in that case, we would get a non-trivial divisor (the neutral element of the multiplicative group of integers $\mod p$, which is $1$).

First of all, we will use SageMath to see whether these conditions hold for our value of $a=8$.

In [20]:
# Define the finite fields of sizes p and q.
# Using these, we can compute orders in the multiplicative groups of the integers mod p and q.
Fp = GF(p)
Fq = GF(q)

In [21]:
# Compute the order of a in both the multiplicative group of integers modulo p and the multiplicative group of integers modulo q.
ord_a_Fp = Fp(a).multiplicative_order()
ord_a_Fq = Fq(a).multiplicative_order()
print("The order of a in Fp* =", ord_a_Fp)
print("The order of a in Fq* =", ord_a_Fq)

The order of a in Fp* = 540
The order of a in Fq* = 244


In [22]:
# Check which of these orders divides s
ord_a_Fp.divides(s), ord_a_Fq.divides(s)

(False, False)

<div class="alert alert-success">
    Thus, we indeed get that the order of $a$ in $F_p^*$ divides $s$, while the order of $a$ in $F_q^*$ does not divide $s$. This implies that the $p-1$ method does indeed work, as expected.
</div>

Next, we will check whether the conditions hold for our alternative value of $a=2$.

In [23]:
# Compute the order of a in both the multiplicative group of integers modulo p and the multiplicative group of integers modulo q.
ord_2_Fp = Fp(2).multiplicative_order()
ord_2_Fq = Fq(2).multiplicative_order()
print("The order of 2 in Fp* =", ord_2_Fp)
print("The order of 2 in Fq* =", ord_2_Fq)

The order of 2 in Fp* = 540
The order of 2 in Fq* = 244


In [24]:
# Check which of these orders divides s
ord_2_Fp.divides(s), ord_2_Fq.divides(s)

(False, False)

<div class="alert alert-warning">
    Here, we see that the order of $a$ in $F_p^*$ does not divide $s$ and that the order of $a$ in $F_q^*$ does not divide $s$. Hence, we indeed see that the $p-1$ method does not work.
</div>

One easy way to see why these orders do or do not divide $s$ is by factorizing them, and then comparing them to the order of $s$:

In [25]:
ord_a_Fp.factor()

2^2 * 3^3 * 5

In [26]:
ord_a_Fq.factor()

2^2 * 61

In [27]:
ord_2_Fp.factor()

2^2 * 3^3 * 5

In [28]:
ord_2_Fq.factor()

2^2 * 61

Similarly, we factor $s$, and obtain:

In [29]:
s.factor()

2^3 * 3^2 * 5 * 7 * 11

Hence, we indeed see that the order of 2 in $F_p^*$ does not divide $s$, while the order of $8$ in $F_p^*$ divides $s$. This difference is attributable to a difference in a factor of $3$ in these orders, which makes sense; since $8 = 2^3$, it should take (if the order of $2$ is divisible by $3$, which it is) three times as many multiplications with $2$ (compared to multiplications with $8$) to arrive at the neutral element of the group.

#### Part 2

For this reasoning, we consider our knowledge of the order of the group, and, in particular, of the divisors of this order.

First, we notice that, if the order of $a$ in $\mathbb{F}_p^*$ divides $s$, we have that $\text{ord}_p(a)\cdot c_s = s$ for some $c_s\in\mathbb{N}$, and where $\text{ord}_p(a)$ is the order of $a$ in $F_p^*$.
Written differently, we obtain
$$\text{ord}_p(a) = \frac{s}{c_s}.$$
Furthermore, since the multiplicative group of integers $\mod p$ is cyclic when $p$ is prime, we know that the order of $a$ is divisible by $p-1$ (the group size; note that this is a different formulation of Fermat's little theorem). Hence, we have that $\text{ord}_p(a) \cdot c_k = p-1$ for some $c_k\in\mathbb{N}$. Written differently, we obtain
$$\text{ord}_p(a) = \frac{p-1}{c_k}.$$

Combining these two equations, we obtain that $$\frac{s}{c_s} = \text{ord}_p(a) = \frac{p-1}{c_k}.$$

Now, this equation has a few interesting properties. Since the order is a natural number (i.e. $\text{ord}_p(a)\in\mathbb{N}$), we must have that both $\frac{s}{c_s}\in\mathbb{N}$ and $\frac{p-1}{c_k}\in\mathbb{N}$. From this, we can conclude that $c_s$ must consist of a subset of the factors of $s$, while $p-1$ must consist of a subset of the factors of $p-1$. Furthermore, since we know that the order of $a$ cannot be $1$ in order for us to obtain a non-trivial divisor of $n$, we must actually have that $c_k$ consists of a strict subset of the factors of $p-1$.

From this, it might become more instructive to write this expression in terms of the factors of $p-1$ and the factors of $s$, which we compute as follows:

In [30]:
s.factor()

2^3 * 3^2 * 5 * 7 * 11

In [31]:
(p-1).factor()

2^2 * 3^3 * 5

We obtain the following expression:
$$\frac{2^3 \cdot 3^2 \cdot 5 \cdot 7\cdot 11}{c_s} = \text{ord}_p(a) = \frac{2^2\cdot 3^3\cdot 5}{c_k}$$

This equation is slightly more informative: we note that, under the constraints described above, we must have that $c_k$ contains at least the factor $3$ for this equation to hold.

Now, let us consider the generator of the multiplicative group of integers $\mod p$, which is given by

In [32]:
Fp.multiplicative_generator()

2

From this, we can easily conclude (since $F_p^*$ is a cyclic group (which holds because $p$ is prime)) that the order of the value $2$ must be $p-1=540$, since the order of a generator is equal to the size of the group.

But this implies that the order of $2$ cannot satisfy the equation given above; $540 = \frac{2^2\cdot 3^3\cdot 5}{c_k}$ if and only if $c_k=1$; this value, however, does not contain the necessary factor of $3$.

For $a=8$, we do not run into this problem; since $8=2^3$, we can easily conclude that the order of $8$ must be the order of $2$ divided by $3$; written as an equation, we have $\text{ord}(8)=\frac{\text{ord}(2)}{3}$. This value can satisfy the equation given above, and hence the value of $8$ does work for the $p-1$ method.

----

Now, there is one more condition to be satisfied: the order of $a$ in the multiplicatie group of integers $\mod q$ should **not** divide $s$.
For this, we can apply a similar reasoning to arrive at the following expression:
$$\frac{2^3 \cdot 3^2 \cdot 5 \cdot 7\cdot 11}{c_s} \neq \text{ord}_q(a) = \frac{2^2\cdot 3\cdot 61}{c_k},$$
where we have used the following factoring of $q-1$:

In [33]:
(q-1).factor()

2^2 * 3 * 61

The inequality on the left-hand side of this epxression holds as long as $c_k$ does not contain the factor $61$. In other words, we must have that the order already contains the factor $61$. _(Otherwise, since the right-hand side of the equation, i.e. $\text{ord}_q(a) = \frac{2^2\cdot 3\cdot 61}{c_k}$ always holds, we would need to have that $c_k$ contains the factor $61$, which implies that a value for $c_s$ exists for which the inequality on the left-hand side is not satisfied.)_

This is not as trivial to see as before, so, in this case, we simply compute the orders and factorize them immediately to see whether this holds:

In [34]:
# Computing the factors of the order of a=8 in Fq*
Fq(8).multiplicative_order().factor()

2^2 * 61

In [35]:
Fq(2).multiplicative_order().factor()

2^2 * 61

In both cases, we see that the factor $61$ is contained in the order of the elements. Hence, we do not run into problems here. This is expected, since neither value of $a$ returned the factor $n$ when running the $p-1$ method.

----

To conclude, let us try to generalize what we have seen just now.

<div class="alert alert-info">
For the $p-1$ method to work, we need the following:
    <ol>
        <li>The order of $a$ in $F_p^*$ <strong>should not</strong> contain the factors which $p-1$ has, but $s$ does not have. <i>(After dividing $s$, $p-1$ and the order of $a$ by the factors which $p-1$ and $s$ have in common.)</i></li>
        <li>The order of $a$ in $F_q^*$ <strong>should</strong> contain (at least one of) the factors which $q-1$ has, but which $s$ does not have <i>(After dividing $s$, $q-1$ and the order of $a$ by the factors which $q-1$ and $s$ have in common.)</i></li>
    </ol>
</div>
Please note that I am not entirely certain about what I have written down above; this is just a simple attempt to generalize the observations made above.

<div class="alert alert-danger">
    Finally, could you give us an indication of what method would be appropriate to use for an exercise like this on the exam? In particular, I am wondering whether the reasoning in part 1 of exercise 3b would suffice, or whether a more elaborate reasoning like that in part 2 is required (and, if so, which parts are necessary and which ones are not).
</div>